### Import Packages

In [1]:
import pathlib
import osmnx as ox
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point, LineString, Polygon
import matplotlib.pyplot as plt
import pyproj
import geodatasets
from shapely import geometry
from pathlib import Path
import folium
import geemap.foliumap as geemap
import ee
import numpy as np
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point
from scipy.spatial import cKDTree
ee.Authenticate()

True

### Define paths and aoi

In [2]:
base = pathlib.Path().resolve()
data = base / "Data"
result = base / "result"

# Define datasets locations

datasets = {
    "corallinales": data / "Corallinales" / "gbif_corallinales_all_20250405",
    "mytilus": data / "Pseudo_absence" / "Mytilus_edulis",
    "zostera": data / "Pseudo_absence" / "Zostera_marina",
    "fucus": data / "Pseudo_absence" / "Fucus_vesiculosus"
}

In [3]:
# Define Scandinavia area of interest
lat_min, lat_max = 54.0, 72.0
lon_min, lon_max = 5.0, 32.0
aoi = [[lat_min, lon_min], [lat_max, lon_max]]

### Read data

In [4]:
# Columns to keep from GBIF datasets
columns = [
    "gbifID", "scientificName", "decimalLatitude", "decimalLongitude",
    "eventDate", "year", "month", "day",
    "locality", "stateProvince", "countryCode", "habitat",
    "basisOfRecord", "recordedBy", "institutionCode", "datasetName",
    "depth", "verbatimDepth", "coordinateUncertaintyInMeters",
    "taxonRank", "kingdom", "phylum", "class", "order", "family", "genus", "species"
]


In [5]:
for name, path in datasets.items():
    df = pd.read_csv(path / "occurrence.txt", sep="\t", usecols=columns, on_bad_lines='skip', low_memory=False)
    globals()[f"df_{name}"] = df 

In [6]:
# check data
print(df_corallinales.head())

       gbifID                           institutionCode datasetName  \
0  2250210127                  Mined from GenBank, NCBI         NaN   
1  1413902398  University of New Brunswick, Fredericton         NaN   
2  2248495107  University of New Brunswick, Fredericton         NaN   
3  2248495299  University of New Brunswick, Fredericton         NaN   
4  1413903418  University of New Brunswick, Fredericton         NaN   

     basisOfRecord                                         recordedBy  \
0  MATERIAL_SAMPLE                                                NaN   
1  MATERIAL_SAMPLE  B. Clarkston, D. McDevit, M. Bruce, A. Savoie,...   
2  MATERIAL_SAMPLE                                   GWS & D. McDevit   
3  MATERIAL_SAMPLE                             B. Clarkston & K. Hind   
4  MATERIAL_SAMPLE                   B. Clarkston, K. Hind & S. Toews   

    eventDate    year  month   day habitat  ... scientificName  kingdom  \
0         NaN     NaN    NaN   NaN     NaN  ...   BOLD:ACD0

### Prepare and sort data

In [7]:
# Reconstruct a reference to each loaded dataframe from global variables
dataframes = {  # create dictionary to store dataframe references
    name: globals()[f"df_{name}"]  # retrieve each dataframe using its constructed variable name
    for name in datasets  # loop through each dataset name
}

In [8]:
# Define colors for each dataset
colors = {
    "corallinales": "red",
    "mytilus": "blue",
    "zostera": "green",
    "fucus": "purple"
}

In [9]:
# Function to clean, filter, and plot GBIF occurrence records by year within a defined AOI
def process_gbif_data(dataframes, lat_min, lat_max, lon_min, lon_max, colors):
    if not isinstance(dataframes, dict):  # check if input is a dictionary
        raise TypeError("Input must be a dictionary of dataframes.")  # raise error for invalid input

    for name, df in dataframes.items():  # loop through each dataset by name
        if not isinstance(df, pd.DataFrame):  # check if value is a valid DataFrame
            print(f" Skipping {name}: Not a valid DataFrame.")  # skip invalid entries
            continue

        # Clean 'year' column
        df.loc[:, "year"] = pd.to_numeric(df["year"], errors="coerce")  # convert year to numeric
        df = df.dropna(subset=["year"])  # remove rows without valid year
        df.loc[:, "year"] = df["year"].astype(int)  # convert year to integer

        # Clean coordinate columns
        df.loc[:, "decimalLatitude"] = pd.to_numeric(df["decimalLatitude"], errors="coerce")  # convert latitude
        df.loc[:, "decimalLongitude"] = pd.to_numeric(df["decimalLongitude"], errors="coerce")  # convert longitude
        df = df.dropna(subset=["decimalLatitude", "decimalLongitude"])  # remove rows with missing coordinates

        # Filter records to Area of Interest (AOI)
        df = df[
            (df["decimalLatitude"] >= lat_min) & (df["decimalLatitude"] <= lat_max) &  # check latitude bounds
            (df["decimalLongitude"] >= lon_min) & (df["decimalLongitude"] <= lon_max)  # check longitude bounds
        ]

        if df.empty:  # check if any records remain after filtering
            print(f" No records found in AOI for {name}, skipping.")  # print skip message
            continue

        # Plot histogram of occurrence records per year
        plt.figure(figsize=(10, 5))  # create figure
        plt.hist(
            df["year"],  # data to plot
            bins=range(int(df["year"].min()), int(df["year"].max()) + 1),  # bin per year
            edgecolor='black',  # border color
            color=colors.get(name, "gray")  # use defined color or default to gray
        )
        plt.title(f"{name.capitalize()} GBIF Records per Year (Scandinavia AOI)")  # add title
        plt.xlabel("Year")  # x-axis label
        plt.ylabel("Number of Records")  # y-axis label
        plt.grid(axis='y', linestyle='--', alpha=0.7)  # add grid
        plt.tight_layout()  # optimize layout

        # Save and display the figure
        filename = f"{name}_gbif_occurrences_per_year.png"  # construct filename
        plt.savefig(filename, dpi=300)  # save figure as PNG
        print(f" Saved: {filename}")  # print confirmation
        plt.show()  # display plot


In [10]:
# Clean and overwrite filtered datasets
for name, df in dataframes.items():  # loop through each dataset by name

    # Convert column types to numeric
    df.loc[:, "year"] = pd.to_numeric(df["year"], errors="coerce")  # convert year
    df.loc[:, "decimalLatitude"] = pd.to_numeric(df["decimalLatitude"], errors="coerce")  # convert latitude
    df.loc[:, "decimalLongitude"] = pd.to_numeric(df["decimalLongitude"], errors="coerce")  # convert longitude

    # Drop rows with missing or invalid values
    df = df.dropna(subset=["year", "decimalLatitude", "decimalLongitude"])  # remove incomplete records

    # Apply filters to keep only relevant records
    df = df[
        (df["year"] >= 2000) &  # filter for year >= 2000
        (df["decimalLatitude"] >= lat_min) & (df["decimalLatitude"] <= lat_max) &  # filter by latitude
        (df["decimalLongitude"] >= lon_min) & (df["decimalLongitude"] <= lon_max)  # filter by longitude
    ]

    # Convert year column to integer
    df.loc[:, "year"] = df["year"].astype(int)  # ensure year is stored as int

    # Overwrite cleaned DataFrame back into the dictionary
    dataframes[name] = df  # update with cleaned and filtered data

    # Print summary of records retained
    print(f"{name.capitalize()} cleaned: {len(df)} records remain")  # confirmation message


Corallinales cleaned: 14466 records remain
Mytilus cleaned: 56577 records remain
Zostera cleaned: 14326 records remain
Fucus cleaned: 57518 records remain


In [11]:
# Remove exact duplicates from each dataset
for name, df in dataframes.items():  # loop through each dataset by name

    # Record original number of rows
    original_count = len(df)  # store initial row count

    # Drop exact duplicate rows
    df_cleaned = df.drop_duplicates()  # remove fully duplicated rows

    # Overwrite cleaned DataFrame back into the dictionary
    dataframes[name] = df_cleaned  # update dataset with cleaned version

    # Report number of duplicates removed and rows remaining
    removed = original_count - len(df_cleaned)  # calculate number of removed rows
    print(f"{name.capitalize()}: Removed {removed} exact duplicate rows ({len(df_cleaned)} remaining).")  # print summary


Corallinales: Removed 0 exact duplicate rows (14466 remaining).
Mytilus: Removed 0 exact duplicate rows (56577 remaining).
Zostera: Removed 0 exact duplicate rows (14326 remaining).
Fucus: Removed 0 exact duplicate rows (57518 remaining).


In [12]:
# Remove strict duplicates based on coordinates and event date
for name, df in dataframes.items():  # loop through each dataset by name

    # Record original number of rows
    original_count = len(df)  # store initial row count

    # Drop strict duplicates: same latitude, longitude, and event date
    df_cleaned = df.drop_duplicates(
        subset=["decimalLatitude", "decimalLongitude", "eventDate"]  # define columns for strict duplication
    )

    # Overwrite cleaned DataFrame back into the dictionary
    dataframes[name] = df_cleaned  # update dataset with cleaned version

    # Report number of strict duplicates removed and rows remaining
    removed = original_count - len(df_cleaned)  # calculate number of removed rows
    print(f"{name.capitalize()}: Removed {removed} location-date duplicates ({len(df_cleaned)} remaining).")  # print summary


Corallinales: Removed 11874 location-date duplicates (2592 remaining).
Mytilus: Removed 34064 location-date duplicates (22513 remaining).
Zostera: Removed 2296 location-date duplicates (12030 remaining).
Fucus: Removed 20266 location-date duplicates (37252 remaining).


In [13]:
# Remove records with missing or empty institutionCode
for name, df in dataframes.items():  # loop through each dataset by name

    # Record original number of rows
    original_count = len(df)  # store initial row count

    # Drop rows where institutionCode is missing (NaN)
    df_cleaned = df.dropna(subset=["institutionCode"])  # remove missing values

    # Drop rows where institutionCode is an empty string
    df_cleaned = df_cleaned[df_cleaned["institutionCode"].str.strip() != ""]  # remove blank strings

    # Overwrite cleaned DataFrame back into the dictionary
    dataframes[name] = df_cleaned  # update dataset with cleaned version

    # Report number of removed records
    removed = original_count - len(df_cleaned)  # calculate number of removed rows
    print(f"{name.capitalize()}: Removed {removed} records without institutionCode.")  # print summary


Corallinales: Removed 759 records without institutionCode.
Mytilus: Removed 7035 records without institutionCode.
Zostera: Removed 3787 records without institutionCode.
Fucus: Removed 21695 records without institutionCode.


In [14]:
# --- Step 1: Load land polygons from Natural Earth ---
land_path = geodatasets.get_path("naturalearth.land")  # get file path for land polygons
land = gpd.read_file(land_path)  # load land polygons as GeoDataFrame

#  Reproject to a projected CRS for Europe (meters) ---
land_projected = land.to_crs("EPSG:3857")  # reproject to Web Mercator for buffering in meters

#  Apply negative buffer (~50 km inland shrink) ---
land_buffered = land_projected.buffer(-50000)  # shrink land polygons by 50,000 meters (50 km)

#  Convert back to WGS84 (EPSG:4326) ---
land_mask = gpd.GeoDataFrame(geometry=land_buffered, crs="EPSG:3857").to_crs("EPSG:4326")  # reproject back

#  Filter land-intersecting points from each dataset ---
for name, df in dataframes.items():  # loop through each dataset by name

    # Convert DataFrame to GeoDataFrame with point geometries
    gdf = gpd.GeoDataFrame(
        df,
        geometry=gpd.points_from_xy(df["decimalLongitude"], df["decimalLatitude"]),  # create point geometry
        crs="EPSG:4326"  # assign WGS84 coordinate system
    )

    # Perform spatial join to identify points intersecting the land mask
    joined = gpd.sjoin(gdf, land_mask, predicate="intersects", how="left")  # tag points falling on land

    # Keep only marine points (those not intersecting land polygons)
    gdf_cleaned = joined[joined["index_right"].isna()].drop(columns=["geometry", "index_right"])  # filter out land hits

    # Overwrite cleaned data in the dictionary
    dataframes[name] = gdf_cleaned  # update dataset with filtered version

    # Report number of land points removed
    removed = len(df) - len(gdf_cleaned)  # calculate number of removed land points
    print(f"{name.capitalize()}: Removed {removed} land points using buffered landmask")  # print summary


Corallinales: Removed 354 land points using buffered landmask
Mytilus: Removed 1948 land points using buffered landmask
Zostera: Removed 369 land points using buffered landmask
Fucus: Removed 945 land points using buffered landmask


In [15]:
# Set filtering parameters ---
min_distance = 3000  # minimum distance in meters from presence points
target_count = int(len(dataframes["corallinales"]) / 3)  # target number of pseudo-absence points per class

#  Convert presence points to projected coordinates ---
gdf_pres = gpd.GeoDataFrame(
    dataframes["corallinales"],  # use presence data
    geometry=gpd.points_from_xy(  # generate point geometry from lon/lat
        dataframes["corallinales"]["decimalLongitude"],
        dataframes["corallinales"]["decimalLatitude"]
    ),
    crs="EPSG:4326"  # original CRS (WGS84)
).to_crs("EPSG:3857")  # reproject to metric CRS for distance calculation

# Extract coordinates of presence points
presence_coords = np.array(list(zip(gdf_pres.geometry.x, gdf_pres.geometry.y)))  # convert to array of x/y tuples

# Loop over each pseudo-absence dataset ---
for name in ["mytilus", "zostera", "fucus"]:  # loop over selected absence datasets

    df_abs = dataframes[name]  # retrieve dataset

    # Convert absence points to projected coordinates
    gdf_abs = gpd.GeoDataFrame(
        df_abs,
        geometry=gpd.points_from_xy(df_abs["decimalLongitude"], df_abs["decimalLatitude"]),  # create geometry
        crs="EPSG:4326"  # original CRS
    ).to_crs("EPSG:3857")  # reproject for spatial filtering

    # Extract coordinates of absence points
    absence_coords = np.array(list(zip(gdf_abs.geometry.x, gdf_abs.geometry.y)))  # convert to array

    # Build KD-tree from presence points
    tree = cKDTree(presence_coords)  # initialize spatial index

    # Calculate distance to nearest presence point for each absence point
    distances, _ = tree.query(absence_coords, k=1)  # find nearest distance

    # Create mask to keep points beyond the minimum distance
    keep_mask = distances >= min_distance  # boolean array
    filtered_df = gdf_abs[keep_mask].copy()  # filter the GeoDataFrame

    # Randomly sample if filtered points exceed target count
    if len(filtered_df) > target_count:
        filtered_df = filtered_df.sample(n=target_count, random_state=42)  # downsample with fixed seed

    # Drop geometry and update dictionary
    dataframes[name] = filtered_df.drop(columns="geometry").copy()  # remove geometry and store

    # Report filtering result
    print(f"{name.capitalize()}: {len(df_abs)} → {len(filtered_df)} (filtered & balanced)")  # print summary


Mytilus: 13530 → 493 (filtered & balanced)
Zostera: 7874 → 493 (filtered & balanced)
Fucus: 14612 → 493 (filtered & balanced)


### Export results to excel files

In [ ]:
# Define output path for Excel file
output_file = result / "institution_summary.xlsx"  # set file path for saving summary

# Create Excel file with a separate sheet for each dataset
with pd.ExcelWriter(output_file) as writer:  # open Excel writer context
    for name, df in dataframes.items():  # loop through each dataset by name

        # Count occurrences of institutionCode (including missing)
        counts = df["institutionCode"].value_counts(dropna=False).rename("count")  # get counts

        # Format as DataFrame with proper column names
        summary = counts.reset_index().rename(columns={"index": "institutionCode"})  # tidy format

        # Write summary to a separate sheet named after the dataset
        summary.to_excel(writer, sheet_name=name.capitalize(), index=False)  # export to Excel

# Print confirmation message
print(f"Saved institution summary to: {output_file}")  # notify user

In [17]:
# Define output Excel file path
excel_path = result / "gbif_filtered_dataframes.xlsx"  # set path for output file

# Save all dataframes to separate sheets in a single Excel file
with pd.ExcelWriter(excel_path, engine="openpyxl") as writer:  # open Excel writer context
    for name, df in dataframes.items():  # loop through each dataset by name

        # Write each DataFrame to a separate sheet named after the dataset
        df.to_excel(writer, sheet_name=name.capitalize(), index=False)  # export without row index

# Print confirmation message
print(f" All dataframes saved to: {excel_path}")  # notify user of save location


✅ All dataframes saved to: C:\Users\rasmu\Desktop\Universitet\Maerl\result\gbif_filtered_dataframes.xlsx


### Visualize data

In [18]:
# Initialize the map centered on Scandinavia
m = geemap.Map(center=[61, 15], zoom=5)  # create interactive map centered on region
m.add_basemap("SATELLITE")  # add satellite basemap layer

# Add bounding box rectangle using the defined Area of Interest (AOI)
folium.Rectangle(
    bounds=aoi,  # list of [southwest, northeast] coordinates
    color="black",  # border color
    weight=2,  # border thickness
    fill=True,  # fill the rectangle
    fill_opacity=0.05,  # make fill slightly transparent
    tooltip="Scandinavia AOI"  # hover text
).add_to(m)  # add rectangle to map

# Plot points from each cleaned dataset
for name, df in dataframes.items():  # loop through each dataset
    print(f"{name.capitalize()} records to plot: {len(df)}")  # print number of points

    for _, row in df.iterrows():  # loop through each row in the dataset

        # Create popup text with scientific name and year (if available)
        popup_text = (
            f"{row['scientificName']} ({row['year']})"
            if pd.notna(row['year']) else row['scientificName']
        )

        # Add circle marker for each record
        folium.CircleMarker(
            location=[row["decimalLatitude"], row["decimalLongitude"]],  # marker position
            radius=3,  # marker size
            color=colors.get(name, "gray"),  # marker color based on dataset
            fill=True,  # enable fill
            fill_opacity=0.6,  # marker transparency
            popup=popup_text  # show scientific name and year
        ).add_to(m)  # add marker to map

# Display the interactive map
m  # render the map


Corallinales records to plot: 1479
Mytilus records to plot: 493
Zostera records to plot: 493
Fucus records to plot: 493


### Export data as geopackage

In [20]:
# Define time slices and corresponding labels
time_slices = {
    "2000_2010": (2000, 2010),  # first decade
    "2010_2020": (2010, 2020),  # second decade
    "2020_2030": (2020, 2030)   # future projection
}

# Loop through all datasets
for name, df in dataframes.items():  # iterate through each dataset

    # Skip datasets without a 'year' column
    if "year" not in df.columns:
        print(f" Skipping {name} — no 'year' column.")  # warn and skip
        continue

    # Retrieve original folder path from the datasets dictionary
    if name in datasets:
        folder = datasets[name]  # get folder path
    else:
        print(f" Could not find folder path for {name}")  # warn if missing
        continue

    # Convert DataFrame to GeoDataFrame with point geometry
    gdf = gpd.GeoDataFrame(
        df,
        geometry=gpd.points_from_xy(df["decimalLongitude"], df["decimalLatitude"]),  # create geometry
        crs="EPSG:4326"  # assign WGS84 coordinate reference system
    )

    # Loop through each time slice
    for label, (start, end) in time_slices.items():  # unpack label and year range

        # Filter records for the current time slice
        gdf_slice = gdf[(gdf["year"] >= start) & (gdf["year"] < end)].copy()  # select records

        if gdf_slice.empty:  # check if result is empty
            print(f"⚠ {name} - {label}: No points found in this range.")  # warn and skip
            continue

        # Define output file path using dataset name and time label
        out_path = folder / f"{name}_{label}.gpkg"  # construct output file path

        # Write filtered GeoDataFrame to GeoPackage
        gdf_slice.to_file(out_path, driver="GPKG")  # export to file
        print(f" Saved: {out_path} ({len(gdf_slice)} records)")  # report result


 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Corallinales\gbif_corallinales_all_20250405\corallinales_2000_2010.gpkg (202 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Corallinales\gbif_corallinales_all_20250405\corallinales_2010_2020.gpkg (640 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Corallinales\gbif_corallinales_all_20250405\corallinales_2020_2030.gpkg (637 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Pseudo_absence\Mytilus_edulis\mytilus_2000_2010.gpkg (50 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Pseudo_absence\Mytilus_edulis\mytilus_2010_2020.gpkg (343 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Pseudo_absence\Mytilus_edulis\mytilus_2020_2030.gpkg (100 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Pseudo_absence\Zostera_marina\zostera_2000_2010.gpkg (64 records)
 Saved: C:\Users\rasmu\Desktop\Universitet\Maerl\Data\Pseudo_absence\Zostera_marina\zostera_2010_2